In [ ]:
import pandas as pd
import plotly.express as px
from IPython.display import display
import numpy as np

pd.set_option('max_rows', 100)
pd.set_option('max_columns', None)

## Events

In [ ]:
activity_columns = ['student_id', 'datetime', 'student_client']

### File Views

In [ ]:
# File Views
fileviews_raw = pd.read_json('./data/BASE B/fileViews.json')
display(fileviews_raw.head())

In [ ]:
fileviews = fileviews_raw.loc[:, ['StudentId', 'ViewDate', 'Studentclient']]
fileviews.columns = activity_columns
fileviews.loc[:, 'event_type'] = 'file_view'
del fileviews_raw

In [ ]:
fileviews.head()

### Questions

In [ ]:
# Questions
questions_raw = pd.read_json('./data/BASE B/questions.json')
display(questions_raw.head())

In [ ]:
questions = questions_raw.loc[:, ['StudentId', 'QuestionDate', 'StudentClient']]
questions.columns = activity_columns
questions.loc[:, 'event_type'] = 'question_created'
del questions_raw

In [ ]:
questions.head()

### Subjects

In [ ]:
subjects_raw = pd.read_json('./data/BASE B/subjects.json')
subjects_raw.head()

In [ ]:
subjects = subjects_raw.loc[:, ['StudentId', 'FollowDate']]
subjects.loc[:, 'StudentClient'] = ''
subjects.columns = activity_columns
subjects.loc[:, 'event_type'] = 'subject_followed'
del subjects_raw

In [ ]:
subjects.loc[subjects['student_id'] == 2774]

### Sessions

In [ ]:
# Load Data
sessions_raw = pd.read_json('./data/BASE B/sessions.json')
sessions_raw.head()

In [ ]:
sessions = sessions_raw.loc[:, ['StudentId', 'SessionStartTime', 'StudentClient']]
sessions.columns = activity_columns
sessions.loc[:, 'event_type'] = 'session_started'
del sessions_raw

### All Events

In [ ]:
activity_df = pd.concat([subjects, questions, fileviews, sessions])
activity_df.columns = ['student_id', 'event_time', 'user_client', 'event_type']
activity_df.head()

In [ ]:
activity_df.to_csv('./data/prep/user_activity_raw.csv', index=False)

### Enrich Activity Data

In [ ]:
activity_df = pd.read_csv('./data/prep/user_activity_raw.csv').sort_values(by=['student_id', 'event_time'])
activity_df.head()

In [ ]:
# Data Prep

# Date/Time columns
activity_df.loc[:, 'event_time'] = pd.to_datetime(activity_df['event_time'], infer_datetime_format=True)
activity_df.loc[:, 'month'] = activity_df['event_time'].astype(str).str[:7]
activity_df.loc[:, 'date'] = activity_df['event_time'].astype(str).str[:10]

activity_df.loc[:, 'day_of_week'] = activity_df['event_time'].dt.weekday
activity_df.loc[:, 'weekday'] = activity_df['day_of_week'].between(1,5)
activity_df.loc[~activity_df['weekday'], 'weekend_date'] = activity_df['date']


activity_df.loc[:, 'event_hour'] = activity_df['event_time'].dt.hour
activity_df.loc[:, 'hour_disc'] = 6*(activity_df['event_hour']/6).astype(int)
activity_df.loc[:, 'period_of_day'] = activity_df['hour_disc'].apply(lambda x: '{}-{}'.format(x, x+5))

# User origin and device
activity_df.loc[:, 'user_origin'] = activity_df['user_client']\
                                        .str.split('|', expand=True).iloc[:, 0]\
                                        .str.strip()\
                                        .str.lower()

activity_df.loc[activity_df['user_origin'].isin(['website']), 'device'] = 'web'
activity_df.loc[~activity_df['user_origin'].isin(['website']), 'device'] = 'mobile'
activity_df.loc[activity_df['user_origin'].isnull(), 'device'] = np.nan

# Window functions
activity_df.loc[:, 'last_event'] = activity_df.groupby(['student_id'])['event_time'].shift(1)
activity_df.loc[:, 'last_event_same_type'] = activity_df.groupby(['student_id', 'event_type'])['event_time'].shift(1)

activity_df.loc[:, 'time_since_last_event'] = ((activity_df['event_time'] - activity_df['last_event']).dt.seconds/3600).fillna(0)
activity_df.loc[:, 'time_since_last_event_type'] = ((activity_df['event_time'] - activity_df['last_event_same_type']).dt.seconds/3600).fillna(0)


In [ ]:
activity_df['device'].value_counts(dropna=False)

In [ ]:
# Save data
activity_df.to_csv('./data/prep/user_activity_prep.csv', index=False)

In [ ]:
del activity_df

### User Event Summary

In [2]:
user_activity = pd.read_csv('./data/prep/user_activity_prep.csv')

user_activity.head()

student_id                  event_time user_client        event_type  \
0        2774  2017-11-02 20:36:23.000000         NaN  subject_followed   
1        2774  2017-11-02 20:36:23.000000         NaN  subject_followed   
2        2774  2017-11-02 20:36:23.000000         NaN  subject_followed   
3        2774  2017-11-02 20:36:23.000000         NaN  subject_followed   
4        2774  2017-11-02 20:36:23.000000         NaN  subject_followed   

                   last_event        last_event_same_type    month  \
0                         NaN                         NaN  2017-11   
1  2017-11-02 20:36:23.000000  2017-11-02 20:36:23.000000  2017-11   
2  2017-11-02 20:36:23.000000  2017-11-02 20:36:23.000000  2017-11   
3  2017-11-02 20:36:23.000000  2017-11-02 20:36:23.000000  2017-11   
4  2017-11-02 20:36:23.000000  2017-11-02 20:36:23.000000  2017-11   

         date  day_of_week  weekday weekend_date  event_hour  hour_disc  \
0  2017-11-02            3     True          NaN          20         18   
1  2017-11-02            3     True          NaN          20         18   
2  2017-11-02            3     True          NaN          20         18   
3  2017-11-02            3     True          NaN          20         18   
4  2017-11-02            3     True          NaN          20         18   

  period_of_day user_origin origin device  delta_last_event  \
0         18-23         NaN    NaN    NaN               NaN   
1         18-23         NaN    NaN    NaN               0.0   
2         18-23         NaN    NaN    NaN               0.0   
3         18-23         NaN    NaN    NaN               0.0   
4         18-23         NaN    NaN    NaN               0.0   

   time_since_last_event  time_since_last_event_type  
0                    0.0                         0.0  
1                    0.0                         0.0  
2                    0.0                         0.0  
3                    0.0                         0.0  
4                    0.0                         0.0

In [3]:
user_activity['event_type'].value_counts(dropna=False)

file_view           3028983
session_started     1399062
subject_followed     315766
question_created       3906
Name: event_type, dtype: int64

In [4]:
user_activity.loc[:, 'is_activity'] = 1
user_activity.loc[user_activity['event_type'] == 'session_started', 'is_activity'] = 0

user_activity.loc[:, 'is_session'] = 0
user_activity.loc[user_activity['event_type'] == 'session_started', 'is_session'] = 1

In [5]:
# Summarize Data - month
activity_month = user_activity\
                    .groupby(['student_id','month'], as_index=True)\
                    .agg({'event_time':['count', 'min', 'max'],
                          'date':'nunique', 
                          'device': 'nunique',
                          'weekend_date':'nunique',
                          'is_activity':'sum'
                         })
activity_month.columns = ['total_events', 'first_event', 'last_event',\
                              'total_days', 'unique_origins', 'days_on_weekend', 'total_activities']
activity_month.head()

total_events                 first_event  \
student_id month                                               
2774       2017-11             9  2017-11-02 20:36:23.000000   
3287       2017-11            10  2017-11-24 13:20:41.000000   
           2017-12             3  2017-12-12 02:03:37.000000   
3546       2015-10             8  2015-10-05 08:56:05.000000   
           2015-11             9  2015-11-03 09:58:54.820000   

                                    last_event  total_days  unique_origins  \
student_id month                                                             
2774       2017-11  2017-11-15 03:01:47.000000           2               1   
3287       2017-11  2017-11-24 16:05:35.000000           1               1   
           2017-12  2017-12-12 02:10:39.000000           1               1   
3546       2015-10  2015-10-14 10:51:29.000000           2               0   
           2015-11  2015-11-17 12:40:02.157000           2               1   

                    days_on_weekend  total_activities  
student_id month                                       
2774       2017-11                0                 7  
3287       2017-11                0                 9  
           2017-12                0                 2  
3546       2015-10                1                 8  
           2015-11                0                 9

In [6]:
# Summarize Data - month, type
activity_type = user_activity\
                    .groupby(['student_id','month', 'event_type'], as_index=True)\
                    .agg({'event_time':'count',
                          'date':'nunique'   
                         })

activity_type.columns = ['events', 'days_used'] 

activity_type = activity_type.unstack().fillna(0)

activity_type.columns = ['{}_{}'.format(c[1].split('_')[0], c[0])
                                                      for c in activity_type.columns.tolist()]

activity_type.head()

file_events  question_events  session_events  \
student_id month                                                   
2774       2017-11          1.0              0.0             2.0   
3287       2017-11          3.0              0.0             1.0   
           2017-12          2.0              0.0             1.0   
3546       2015-10          0.0              0.0             0.0   
           2015-11          0.0              7.0             0.0   

                    subject_events  file_days_used  question_days_used  \
student_id month                                                         
2774       2017-11             6.0             1.0                 0.0   
3287       2017-11             6.0             1.0                 0.0   
           2017-12             0.0             1.0                 0.0   
3546       2015-10             8.0             0.0                 0.0   
           2015-11             2.0             0.0                 2.0   

                    session_days_used  subject_days_used  
student_id month                                          
2774       2017-11                2.0                1.0  
3287       2017-11                1.0                1.0  
           2017-12                1.0                0.0  
3546       2015-10                0.0                2.0  
           2015-11                0.0                1.0

In [7]:
# Summarize Data - month, device

activity_device = user_activity\
                    .groupby(['student_id','month', 'device'], as_index=True)\
                    .agg({'event_time':'count',
                          'date':'nunique'   
                         })

activity_device.columns = ['events_on', 'used_days_on'] 

activity_device = activity_device.unstack().fillna(0)

activity_device.columns = ['{}_{}'.format(c[0], c[1]) for c in activity_device.columns.tolist()]

activity_device.head()

events_on_mobile  events_on_web  used_days_on_mobile  \
student_id month                                                           
2774       2017-11               0.0            3.0                  0.0   
3287       2017-11               0.0            4.0                  0.0   
           2017-12               0.0            3.0                  0.0   
3546       2017-11               0.0           12.0                  0.0   
           2017-12               0.0            1.0                  0.0   

                    used_days_on_web  
student_id month                      
2774       2017-11               2.0  
3287       2017-11               1.0  
           2017-12               1.0  
3546       2017-11               2.0  
           2017-12               1.0

In [11]:
# Summarize Data - month, period
activity_period = user_activity\
                    .groupby(['student_id','month', 'period_of_day'], as_index=True)\
                    .agg({'event_time':'count'})

activity_period.columns = ['events_usage__']

activity_period = activity_period.unstack().fillna(0)

activity_period.columns = [c[0] + c[1] for c in activity_period.columns.tolist()]

activity_period.head()

events_usage__0-5  events_usage__12-17  \
student_id month                                             
2774       2017-11                1.0                  0.0   
3287       2017-11                0.0                 10.0   
           2017-12                3.0                  0.0   
3546       2015-10                0.0                  0.0   
           2015-11                0.0                  5.0   

                    events_usage__18-23  events_usage__6-11  
student_id month                                             
2774       2017-11                  8.0                 0.0  
3287       2017-11                  0.0                 0.0  
           2017-12                  0.0                 0.0  
3546       2015-10                  0.0                 8.0  
           2015-11                  0.0                 4.0

In [13]:
user_monthly_summary = activity_month\
                        .join(activity_type, how='left')\
                        .join(activity_device, how='left')\
                        .join(activity_period, how='left')\
                        .fillna(0)\
                        .reset_index()

user_monthly_summary.head()

student_id    month  total_events                 first_event  \
0        2774  2017-11             9  2017-11-02 20:36:23.000000   
1        3287  2017-11            10  2017-11-24 13:20:41.000000   
2        3287  2017-12             3  2017-12-12 02:03:37.000000   
3        3546  2015-10             8  2015-10-05 08:56:05.000000   
4        3546  2015-11             9  2015-11-03 09:58:54.820000   

                   last_event  total_days  unique_origins  days_on_weekend  \
0  2017-11-15 03:01:47.000000           2               1                0   
1  2017-11-24 16:05:35.000000           1               1                0   
2  2017-12-12 02:10:39.000000           1               1                0   
3  2015-10-14 10:51:29.000000           2               0                1   
4  2015-11-17 12:40:02.157000           2               1                0   

   total_activities  file_events  question_events  session_events  \
0                 7          1.0              0.0             2.0   
1                 9          3.0              0.0             1.0   
2                 2          2.0              0.0             1.0   
3                 8          0.0              0.0             0.0   
4                 9          0.0              7.0             0.0   

   subject_events  file_days_used  question_days_used  session_days_used  \
0             6.0             1.0                 0.0                2.0   
1             6.0             1.0                 0.0                1.0   
2             0.0             1.0                 0.0                1.0   
3             8.0             0.0                 0.0                0.0   
4             2.0             0.0                 2.0                0.0   

   subject_days_used  events_on_mobile  events_on_web  used_days_on_mobile  \
0                1.0               0.0            3.0                  0.0   
1                1.0               0.0            4.0                  0.0   
2                0.0               0.0            3.0                  0.0   
3                2.0               0.0            0.0                  0.0   
4                1.0               0.0            7.0                  0.0   

   used_days_on_web  events_usage__0-5  events_usage__12-17  \
0               2.0                1.0                  0.0   
1               1.0                0.0                 10.0   
2               1.0                3.0                  0.0   
3               0.0                0.0                  0.0   
4               2.0                0.0                  5.0   

   events_usage__18-23  events_usage__6-11  
0                  8.0                 0.0  
1                  0.0                 0.0  
2                  0.0                 0.0  
3                  0.0                 8.0  
4                  0.0                 4.0

In [14]:
user_monthly_summary.to_csv('./data/prep/user_activity_summary.csv', index=False)

## Payments

In [ ]:
premium_payments = pd.read_json('./data/BASE B/premium_payments.json')

premium_payments.columns = ['student_id', 'created_at', 'plan_type']
premium_payments.loc[:, 'plan_id'] = premium_payments['student_id'].astype(str) + '_' +\
                                    premium_payments['plan_type'] + '_' +\
                                    premium_payments['created_at'].str[:10]

premium_payments.loc[:, 'event_type'] = 'payment'
premium_payments.head()

In [ ]:
premium_payments['created_at'].max()

In [ ]:
premium_cancellations = pd.read_json('./data/BASE B/premium_cancellations.json')

premium_cancellations.columns = ['student_id', 'created_at']

premium_cancellations.loc[:, 'plan_type'] = ''
premium_cancellations.loc[:, 'plan_id'] = ''
premium_cancellations.loc[:, 'event_type'] = 'cancelation'

In [ ]:
premium_cancellations.shape

In [ ]:
plan_events = pd\
                .concat([premium_cancellations, premium_payments], axis=0)\
                .sort_values(by=['student_id', 'created_at'])\
                .reset_index().drop(columns=['index'])

plan_events.loc[:, 'last_plan_id'] = plan_events\
                                        .groupby(['student_id'])['plan_id'].shift(1)


plan_events.loc[plan_events['event_type'] == 'cancelation', 'plan_id'] =  plan_events['last_plan_id']

cancellations_adj = plan_events\
                        .loc[plan_events['event_type'] == 'cancelation']\
                        .loc[:, ['plan_id', 'created_at']].set_index('plan_id')

cancellations_adj.columns = ['cancelled_at']
    
plans = premium_payments.set_index('plan_id')\
            .join(cancellations_adj, how='left', rsuffix='_cancel')\
            .reset_index()\
            .iloc[:, [0, 1, 2, 3, 5]]

plans.loc[plans['plan_type'] == 'Mensal', 'cost'] = 29.9
plans.loc[plans['plan_type'] == 'Anual', 'cost'] = 286.8
                                                        
(~plans.isnull()).sum()

In [ ]:
# Check inconsistency
plan_events.loc[plan_events['event_type'] == 'cancelation', 'last_plan_id'].isnull().sum()

There are 46 plans that do not appear on the premium plans table.

In [ ]:
plans.head()

In [ ]:
# Save data
plans.to_csv('./data/prep/premium_plans_info.csv', index=False)

In [ ]:
# Load data
plans = pd.read_csv('./data/prep/premium_plans_info.csv')

## Students

In [120]:
# Load Data
students_raw = pd.read_json('./data/BASE B/students.json')
students_raw.head()

Id              RegisteredDate UniversityName  \
0  12970655  2012-05-29 15:22:27.490000        PUC-RIO   
1  59873654  2012-09-03 20:32:04.853000            UFF   
2   3664695  2012-09-10 20:26:30.253000            UNB   
3  15207697  2012-09-05 15:31:08.090000           UERJ   
4  36988693  2012-10-15 21:34:51.143000            UFU   

                               CourseName             State SignupSource  \
0                           Administração    Rio de Janeiro        Email   
1  Direito do Trabalho e Segurança Social    Rio de Janeiro     Facebook   
2                              Enfermagem  Distrito Federal     Facebook   
3         Engenharia de Produção Mecânica    Rio de Janeiro     Facebook   
4                     Engenharia Elétrica               NaN     Facebook   

             City StudentClient  
0             NaN           NaN  
1  Rio de Janeiro           NaN  
2             NaN           NaN  
3         Resende           NaN  
4             NaN           NaN

In [121]:
students_raw.isnull().mean()

Id                0.000000
RegisteredDate    0.000000
UniversityName    0.000000
CourseName        0.000000
State             0.596017
SignupSource      0.000000
City              0.669500
StudentClient     0.140317
dtype: float64

In [150]:
# Data Prep
students_raw.loc[:, 'user_origin'] = students_raw['StudentClient']\
                            .str.split('|', expand=True).iloc[:, 0]\
                            .str.strip().str.lower()

students_raw.loc[~students_raw['user_origin'].isnull(), 'origin'] = 'other'
students_raw.loc[students_raw['user_origin'].isin(['website', 'ios', 'android']), 'origin'] = students_raw['user_origin']

In [151]:
students_raw['origin'].value_counts()

website    38316
android     7401
other       3725
ios         2139
Name: origin, dtype: int64

In [147]:
fig = px.histogram(students_raw, x=['RegisteredDate', 'SignupSource', 'State'], facet_col='variable',
                   title='Distribuição de variáveis do usuário')

fig.update_yaxes(matches=None, showticklabels=True)
fig.update_layout(showlegend=False)
fig.show()

### Course Area

In [89]:
# Exploring course distribution
df = students_raw\
        .groupby(['CourseName'], as_index=False)\
        .agg({'Id':'count'})\
        .sort_values(by='Id', ascending=False)

df.columns = ['course', 'students']
df['cumul_students'] = df['students'].cumsum()
df['total_students'] = df['students'].sum()
df['rank'] = df['students'].rank(ascending=False)

df.loc[:, 'cumul_percentage'] = 100*df['cumul_students']/df['total_students']
df.loc[:, 'percentage'] = 100*df['students']/df['total_students']

df.head()

fig = px.area(df, x='rank', y='cumul_percentage', hover_name='course', hover_data=['students', 'percentage'])
fig.show()

df.head(40)

course  students  cumul_students  \
100                                Direito      9862            9862   
0                            Administração      4099           13961   
139                       Engenharia Civil      3585           17546   
85      Contabilidade / Ciências Contábeis      2744           20290   
363                              Pedagogia      2627           22917   
388                             Psicologia      2155           25072   
122                             Enfermagem      2054           27126   
340                               Medicina      1656           28782   
206                           Fisioterapia      1464           30246   
155                    Engenharia Mecânica      1451           31697   
357                               Nutrição      1297           32994   
203      Farmácia / Ciências Farmacêuticas      1142           34136   
111                        Educação Física      1076           35212   
185                 Engenharia de Produção      1053           36265   
360                            Odontologia       985           37250   
143                    Engenharia Elétrica       957           38207   
469     Veterinária / Medicina Veterinária       890           39097   
38          Biologia / Ciências Biológicas       753           39850   
16                 Arquitetura e Urbanismo       724           40574   
245             Gestão de Recursos Humanos       645           41219   
160                     Engenharia Química       628           41847   
421                         Serviço Social       605           42452   
40                             Biomedicina       561           43013   
11   Análise e Desenvolvimento de Sistemas       549           43562   
48                   Ciência da Computação       450           44012   
332                             Matemática       448           44460   
426   Sistemas de Informação / Informática       433           44893   
391                                Química       424           45317   
106         Economia / Ciências Econômicas       396           45713   
8                                Agronomia       346           46059   
273           Letras e Línguas - Português       319           46378   
131                   Engenharia Ambiental       295           46673   
141          Engenharia Civil e Ambiental        289           46962   
163               Engenharia da Computação       282           47244   
324                              Logística       276           47520   
314             Licenciatura em Matemática       263           47783   
255                               História       257           48040   
300        Licenciatura em Educação Física       255           48295   
142                  Engenharia Eletrônica       235           48530   
331                              Marketing       230           48760   

     total_students  rank  cumul_percentage  percentage  
100           60000   1.0         16.436667   16.436667  
0             60000   2.0         23.268333    6.831667  
139           60000   3.0         29.243333    5.975000  
85            60000   4.0         33.816667    4.573333  
363           60000   5.0         38.195000    4.378333  
388           60000   6.0         41.786667    3.591667  
122           60000   7.0         45.210000    3.423333  
340           60000   8.0         47.970000    2.760000  
206           60000   9.0         50.410000    2.440000  
155           60000  10.0         52.828333    2.418333  
357           60000  11.0         54.990000    2.161667  
203           60000  12.0         56.893333    1.903333  
111           60000  13.0         58.686667    1.793333  
185           60000  14.0         60.441667    1.755000  
360           60000  15.0         62.083333    1.641667  
143           60000  16.0         63.678333    1.595000  
469           60000  17.0         65.161667    1.483333  
38            60000  18.0         66.41

In [134]:
course_map = {
    'Direito': ['Direito'],
    'Administração': ['Administração', 'Gestão'],
    'Engenharia': ['Engenharia'],
    'Biológicas': ['Enfermagem', 'Medicina', 'Fisioterapia', 'Nutrição', 
                      'Farmácia', 'Educação Física', 'Biologia', 'Saúde',
                      'Odontologia', 'Veterinária', 'Biomedicina'],
    'Humanas': ['Psicologia', 'Pedagogia', 'Arquitetura', 'História', 'Arte',
                'Geografia', 'Letras', 'Marketing', 'Comunicação'],
    'Exatas': ['Contabilidade', 'Sistemas', 'Química', 'Economia', 'Agronomia', 'Logística', 
               'Matemática', 'Física', 'Tecnologia', 'Informação']
}

def get_course_classification(name):
    for macro_class, courses in course_map.items():
        for c in courses:
            if c.lower() in name.lower():
                return macro_class
            
    if name:
        return 'Outros'

students_area = students_raw.copy()

students_area.loc[:, 'course_area'] = students_area['CourseName'].apply(lambda x: get_course_classification(x))

students_area.groupby(['course_area', 'CourseName']).agg({'Id':'count'})

students_area = students_area.set_index('Id').loc[:, ['course_area']]

In [138]:
students_area['course_area'].value_counts(dropna=False)

Biológicas       12561
Engenharia       10891
Direito          10040
Humanas           8239
Exatas            7437
Administração     6338
Outros            4494
Name: course_area, dtype: int64

### University

In [92]:
# Exploring university distribution
df = students_raw\
        .groupby(['UniversityName'], as_index=False)\
        .agg({'Id':'count'})\
        .sort_values(by='Id', ascending=False)

df.columns = ['university', 'students']
df['cumul_students'] = df['students'].cumsum()
df['total_students'] = df['students'].sum()
df['rank'] = df['students'].rank(ascending=False)

df.loc[:, 'cumul_percentage'] = 100*df['cumul_students']/df['total_students']
df.loc[:, 'percentage'] = 100*df['students']/df['total_students']

fig = px.area(df, x='rank', y='cumul_percentage', hover_name='university', hover_data=['students', 'percentage'])
fig.show()

df.head(20)

university  students  cumul_students  total_students  rank  \
178                ESTÁCIO      8919            8919           60000   1.0   
1513                  UNIP      4392           13311           60000   2.0   
1590                UNOPAR      1784           15095           60000   3.0   
1511               UNINTER      1780           16875           60000   4.0   
179            ESTÁCIO EAD      1446           18321           60000   5.0   
1414  UNIDERP - ANHANGUERA       671           18992           60000   6.0   
33              Anhanguera       660           19652           60000   7.0   
1615                USP-SP       601           20253           60000   8.0   
1173             PITÁGORAS       556           20809           60000   9.0   
1315                  UFRJ       530           21339           60000  10.0   
1344                   UNB       472           21811           60000  11.0   
1510               UNINOVE       470           22281           60000  12.0   
1300                  UFMG       419           22700           60000  13.0   
1576              UNIVERSO       374           23074           60000  14.0   
1308                  UFPE       371           23445           60000  15.5   
1180             PUC-MINAS       371           23816           60000  15.5   
1293                   UFF       355           24171           60000  17.0   
1357                 UNESP       320           24491           60000  18.0   
1287                   UFC       314           24805           60000  19.0   
1621                   UVA       310           25115           60000  20.0   

      cumul_percentage  percentage  
178          14.865000   14.865000  
1513         22.185000    7.320000  
1590         25.158333    2.973333  
1511         28.125000    2.966667  
179          30.535000    2.410000  
1414         31.653333    1.118333  
33           32.753333    1.100000  
1615         33.755000    1.001667  
1173         34.681667    0.926667  
1315         35.565000    0.883333  
1344         36.351667    0.786667  
1510         37.135000    0.783333  
1300         37.833333    0.698333  
1576         38.456667    0.623333  
1308         39.075000    0.618333  
1180         39.693333    0.618333  
1293         40.285000    0.591667  
1357         40.818333    0.533333  
1287         41.341667    0.523333  
1621         41.858333    0.516667

In [93]:
top_20_uni = df.loc[df['rank'] <= 20, 'university'].tolist()

In [94]:
student_university = students_raw.copy()
student_university.loc[:, 'on_top_20_university'] = student_university['UniversityName']\
                                                        .apply(lambda x: x in top_20_uni)

student_university = student_university.set_index('Id').loc[:, ['on_top_20_university']]
student_university.head()

on_top_20_university
Id                            
12970655                 False
59873654                  True
3664695                   True
15207697                 False
36988693                 False

### Region

In [95]:
states = pd.read_csv('./data/estados.csv')
regions = pd.read_csv('./data/regioes.csv')

states_infos = pd.merge(left=states, right=regions, left_on='Regiao', right_on='Id', suffixes=('_state', '_region'))

states_infos.loc[:, 'state_name'] = states_infos['Nome_state']\
                                        .str.lower()\
                                        .str.replace(' ', '_')\
                                        .str.normalize('NFKD')\
                                        .str.encode('ascii', errors='ignore')\
                                        .str.decode('utf-8')

states_infos.loc[:, 'region'] = states_infos['Nome_region']

state_region_dict = states_infos.set_index('state_name')['region'].to_dict()

state_region_dict

{'acre': 'Norte',
 'amapa': 'Norte',
 'amazonas': 'Norte',
 'para': 'Norte',
 'rondonia': 'Norte',
 'roraima': 'Norte',
 'tocantins': 'Norte',
 'alagoas': 'Nordeste',
 'bahia': 'Nordeste',
 'ceara': 'Nordeste',
 'maranhao': 'Nordeste',
 'paraiba': 'Nordeste',
 'pernambuco': 'Nordeste',
 'piaui': 'Nordeste',
 'rio_grande_do_norte': 'Nordeste',
 'sergipe': 'Nordeste',
 'distrito_federal': 'Centro-Oeste',
 'goias': 'Centro-Oeste',
 'mato_grosso': 'Centro-Oeste',
 'mato_grosso_do_sul': 'Centro-Oeste',
 'espirito_santo': 'Sudeste',
 'minas_gerais': 'Sudeste',
 'rio_de_janeiro': 'Sudeste',
 'sao_paulo': 'Sudeste',
 'parana': 'Sul',
 'rio_grande_do_sul': 'Sul',
 'santa_catarina': 'Sul'}

In [140]:
students_region = students_raw.copy()
students_region.loc[:, 'state_name'] = students_region['State']\
                                                .str.lower()\
                                                .str.replace(' ', '_')\
                                                .str.normalize('NFKD')\
                                                .str.encode('ascii', errors='ignore')\
                                                .str.decode('utf-8')\
                                                .fillna('')

students_region.loc[:, 'region'] = students_region['state_name'].apply(lambda x: state_region_dict[x] if x else np.nan)

students_region = students_region.set_index('Id').loc[:, ['region']]

In [141]:
students_region['region'].value_counts()

Sudeste         11997
Nordeste         5636
Sul              3358
Centro-Oeste     1808
Norte            1440
Name: region, dtype: int64

### Payment

In [157]:
plans = pd.read_csv('./data/prep/premium_plans_info.csv')

plans.head()

plan_id  student_id                  created_at  \
0  10015104_Mensal_2017-11-05    10015104  2017-11-05 20:21:08.382446   
1  10015104_Mensal_2017-12-05    10015104  2017-12-05 09:27:20.376543   
2  10015104_Mensal_2018-05-20    10015104  2018-05-20 12:39:21.000000   
3  10079710_Mensal_2017-06-13    10079710  2017-06-13 16:59:33.587138   
4  10079710_Mensal_2017-07-13    10079710  2017-07-13 09:04:34.299575   

  plan_type                cancelled_at  cost  
0    Mensal                         NaN  29.9  
1    Mensal  2017-12-13 18:33:35.230373  29.9  
2    Mensal                         NaN  29.9  
3    Mensal                         NaN  29.9  
4    Mensal                         NaN  29.9

In [164]:
not_cancelled_plans = plans.loc[plans['cancelled_at'].isnull()].copy()

not_cancelled_plans.loc[:, 'first'] = not_cancelled_plans.groupby(['student_id'])['created_at'].transform('min')
not_cancelled_plans.loc[:, 'revenue_first_plan'] = 0
not_cancelled_plans.loc[not_cancelled_plans['created_at'] == not_cancelled_plans['first'], 'revenue_first_plan'] = not_cancelled_plans['cost']


plans_per_user = not_cancelled_plans\
                    .groupby(['student_id'], as_index=True)\
                    .agg({'plan_id':'count', 'cost':'sum', 'created_at':['min', 'max'], 'revenue_first_plan':'sum'})

plans_per_user.columns = ['total_plans', 'ltv', 'first_purchase', 'last_purchase', 'revenue_first_purchase']
plans_per_user.head()

not_cancelled_plans

plan_id  student_id                  created_at  \
0     10015104_Mensal_2017-11-05    10015104  2017-11-05 20:21:08.382446   
2     10015104_Mensal_2018-05-20    10015104  2018-05-20 12:39:21.000000   
3     10079710_Mensal_2017-06-13    10079710  2017-06-13 16:59:33.587138   
4     10079710_Mensal_2017-07-13    10079710  2017-07-13 09:04:34.299575   
5     10079710_Mensal_2017-08-13    10079710  2017-08-13 08:52:28.026018   
...                          ...         ...                         ...   
7270   9987275_Mensal_2018-04-13     9987275  2018-04-13 09:30:14.000000   
7271   9987275_Mensal_2018-05-13     9987275  2018-05-13 10:53:09.000000   
7272  99892099_Mensal_2018-04-19    99892099  2018-04-19 22:21:02.000000   
7273  99892099_Mensal_2018-05-19    99892099  2018-05-19 10:09:14.000000   
7274  99946491_Mensal_2017-12-04    99946491  2017-12-04 19:52:45.972339   

     plan_type cancelled_at  cost                       first  \
0       Mensal          NaN  29.9  2017-11-05 20:21:08.382446   
2       Mensal          NaN  29.9  2017-11-05 20:21:08.382446   
3       Mensal          NaN  29.9  2017-06-13 16:59:33.587138   
4       Mensal          NaN  29.9  2017-06-13 16:59:33.587138   
5       Mensal          NaN  29.9  2017-06-13 16:59:33.587138   
...        ...          ...   ...                         ...   
7270    Mensal          NaN  29.9  2017-11-13 20:45:55.511362   
7271    Mensal          NaN  29.9  2017-11-13 20:45:55.511362   
7272    Mensal          NaN  29.9  2018-04-19 22:21:02.000000   
7273    Mensal          NaN  29.9  2018-04-19 22:21:02.000000   
7274    Mensal          NaN  29.9  2017-12-04 19:52:45.972339   

      revenue_first_plan  
0                   29.9  
2                    0.0  
3                   29.9  
4                    0.0  
5                    0.0  
...                  ...  
7270                 0.0  
7271                 0.0  
7272                29.9  
7273                 0.0  
7274                29.9  

[6488 rows x 8 columns]

### Final Dataset

In [165]:
students_raw.head()

Id              RegisteredDate UniversityName  \
0  12970655  2012-05-29 15:22:27.490000        PUC-RIO   
1  59873654  2012-09-03 20:32:04.853000            UFF   
2   3664695  2012-09-10 20:26:30.253000            UNB   
3  15207697  2012-09-05 15:31:08.090000           UERJ   
4  36988693  2012-10-15 21:34:51.143000            UFU   

                               CourseName             State SignupSource  \
0                           Administração    Rio de Janeiro        Email   
1  Direito do Trabalho e Segurança Social    Rio de Janeiro     Facebook   
2                              Enfermagem  Distrito Federal     Facebook   
3         Engenharia de Produção Mecânica    Rio de Janeiro     Facebook   
4                     Engenharia Elétrica               NaN     Facebook   

             City StudentClient user_origin origin  
0             NaN           NaN         NaN    NaN  
1  Rio de Janeiro           NaN         NaN    NaN  
2             NaN           NaN         NaN    NaN  
3         Resende           NaN         NaN    NaN  
4             NaN           NaN         NaN    NaN

In [166]:
students_renamed = students_raw.copy().set_index('Id')
students_renamed.columns = ['signup_at', 'university_name', 'course_name', 'state', 'signup_source', 'city', 'user_client', 'user_origin', 'origin']

students = pd.concat([students_renamed, students_area, student_university, students_region, plans_per_user], axis=1)

students.loc[:, 'has_purchased'] = ~students['first_purchase'].isnull()

students.loc[:, 'on_top_20_university'] = students['on_top_20_university'].fillna(False)

students.index.name = 'student_id'
students.head()

signup_at university_name  \
student_id                                               
2774        2017-11-02 22:33:13.199000        UNINORTE   
3287        2017-11-24 13:19:30.684799            UNIP   
3546        2014-01-09 07:56:11.830000         ESTÁCIO   
7251        2017-04-20 14:54:38.956966        UNIFAVIP   
7338        2016-06-05 12:25:46.003000         ESTÁCIO   

                         course_name           state signup_source  \
student_id                                                           
2774        Licenciatura em Biologia        Amazonas      Facebook   
3287                   Administração             NaN        Google   
3546                         Direito           Piauí      Facebook   
7251             Engenharia Mecânica             NaN        Google   
7338                Engenharia Civil  Rio de Janeiro        Google   

                      city user_client user_origin   origin    course_area  \
student_id                                                                   
2774                Manaus     Website     website  website     Biológicas   
3287                   NaN     Website     website  website  Administração   
3546                   NaN         NaN         NaN      NaN        Direito   
7251                   NaN         NaN         NaN      NaN     Engenharia   
7338        Rio de Janeiro     Website     website  website     Engenharia   

            on_top_20_university    region  total_plans  ltv first_purchase  \
student_id                                                                    
2774                       False     Norte          NaN  NaN            NaN   
3287                        True       NaN          NaN  NaN            NaN   
3546                        True  Nordeste          NaN  NaN            NaN   
7251                       False       NaN          NaN  NaN            NaN   
7338                        True   Sudeste          NaN  NaN            NaN   

           last_purchase  revenue_first_purchase  has_purchased  
student_id                                                       
2774                 NaN                     NaN          False  
3287                 NaN                     NaN          False  
3546                 NaN                     NaN          False  
7251                 NaN                     NaN          False  
7338                 NaN                     NaN          False

In [167]:
students['origin'].value_counts()

website    38316
android     7401
other       3725
ios         2139
Name: origin, dtype: int64

In [168]:
students.isnull().mean()

signup_at                 0.000000
university_name           0.000000
course_name               0.000000
state                     0.596017
signup_source             0.000000
city                      0.669500
user_client               0.140317
user_origin               0.140317
origin                    0.140317
course_area               0.000000
on_top_20_university      0.000000
region                    0.596017
total_plans               0.970950
ltv                       0.970950
first_purchase            0.970950
last_purchase             0.970950
revenue_first_purchase    0.970950
has_purchased             0.000000
dtype: float64

In [169]:
students.to_csv('./data/prep/user_infos.csv', index=True)